## KAKAOMAP 상세보기 리뷰 가져오기

In [3]:
from selenium import webdriver
from selenium.webdriver.common.keys import Keys
from selenium.webdriver.common.by import By
from selenium.webdriver.chrome.service import Service
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC
from webdriver_manager.chrome import ChromeDriverManager
from bs4 import BeautifulSoup
import time
import pandas as pd
import numpy as np
import re
import sys

import warnings
warnings.filterwarnings('ignore')


In [ ]:
## 상세보기(moreview) 리스트 CSV 파일 불러오기
df = pd.read_csv('kakaomap_yeonnam_restaurant_moreview_list(0529).csv') #, encoding='cp949')
df

사업장명                소재지전체주소                                도로명전체주소  \
0          사르르  서울특별시 마포구 연남동 383-100           서울특별시 마포구 연희로1길 63, 2층 (연남동)   
1    빨강꼬치&꼬떡상회   서울특별시 마포구 연남동 390-71         서울특별시 마포구 동교로38길 13, 지1층 (연남동)   
2          지라파   서울특별시 마포구 연남동 373-12              서울특별시 마포구 연남로 8, 1층 (연남동)   
3          돈토키   서울특별시 마포구 연남동 390-28  서울특별시 마포구 동교로38길 27-19, 지층 B02호 (연남동)   
4     에스유 치즈카페   서울특별시 마포구 연남동 225-29         서울특별시 마포구 성미산로 175, 지하1층 (연남동)   
..         ...                    ...                                    ...   
795       연남제비    서울특별시 마포구 연남동 228-5           서울특별시 마포구 성미산로 186 (연남동, 1층)   
796   유키모찌 연남점   서울특별시 마포구 연남동 260-28             서울특별시 마포구 동교로 240 (연남동,1층)   
797   항저우 샤롱바오   서울특별시 마포구 연남동 568-23         서울특별시 마포구 동교로27길 41 (연남동,(1층))   
798     뭉텅 연남점    서울특별시 마포구 연남동 228-1           서울특별시 마포구 성미산로 190 (연남동, 1층)   
799        코리아  서울특별시 마포구 연남동 227-1번지              서울특별시 마포구 연희로 35 (연남동,1층)   

     좌표정보X(EPSG5174)  좌표정보Y(EPSG5174)                                 상세보기url  
0      193442.684557    451030.233681                                     NaN  
1      193303.524530    451089.391094   https://place.map.kakao.com/243028981  
2      193169.497265    450929.132987                                     NaN  
3      193388.640488    451076.653833                                     NaN  
4      193333.879086    451308.487923                                     NaN  
..               ...              ...                                     ...  
795    193391.074652    451202.033340  https://place.map.kakao.com/2045155753  
796    193255.606492    451004.993797   https://place.map.kakao.com/913195358  
797    192990.763157    450825.627592   https://place.map.kakao.com/961577779  
798    193406.589452    451183.710005   https://place.map.kakao.com/388449263  
799    193478.255108    451077.631725    https://place.map.kakao.com/15742085  

[800 rows x 6 columns]

In [5]:
df['상세보기url'].count()

np.int64(695)

In [6]:
## DF에서 NaN 또는 빈 문자열을 제외한 값만 리스트로 변환
url_list = df['상세보기url'].dropna().tolist()  # NaN 제거
url_list = [url for url in url_list if url.strip()]  # 빈 문자열 제거

# # 결과 출력
# print(url_list)

In [7]:
## 생성한 리스트에 빈 문자열 또는 NaN 값이 있는지 검증
has_empty_or_nan = any(item == "" or item is None or (isinstance(item, float) and np.isnan(item)) for item in url_list)
print("리스트에 빈 문자열 또는 NaN이 포함되어 있나요?", has_empty_or_nan)

리스트에 빈 문자열 또는 NaN이 포함되어 있나요? False


In [8]:
## 리스트 갯수(길이) 확인
len(url_list)

695

In [ ]:
## 리뷰 가져오기 준비 준비

## 리뷰 저장용 DF 생성
review_df = pd.DataFrame(columns=['사업장명',
                                  '분류',
                                  '카카오맵ID',
                                  '리뷰어이름',
                                  '리뷰어레벨',
                                  '후기개수',
                                  '별점평균',
                                  '팔로워수',
                                  '작성일',
                                  '별점',
                                  '리뷰내용',
                                  '사진URL'
                                  ])

## 웹드라이버 설정
service = Service(ChromeDriverManager().install())
driver = webdriver.Chrome(service=service)
# time.sleep(2)

In [ ]:
## 카카오맵 검색 가게 후기 가져오기 ### (250527이전)

## 리뷰 스크래핑 함수
def all_review_scraping(temp_rev, rev_cnt):
    global store_name, store_category, store_id
    temp_rev_list = []
    
    # 리뷰어 이름
    reviewer_name_tag = temp_rev.select_one('.name_user')
    reviewer_name = reviewer_name_tag.contents[1].strip() if reviewer_name_tag and len(reviewer_name_tag.contents) > 1 else "N/A"
    
    # 리뷰어 레벨
    reviewer_level_tag = temp_rev.select_one('.txt_badge')
    reviewer_level = reviewer_level_tag.text.replace('레벨', '').strip() if reviewer_level_tag else "N/A"
    
    # 후기, 별점평균, 팔로워 수 (list_detail 활용)
    review_stats = {}
    list_detail = temp_rev.select_one('.list_detail')
    if list_detail:
        items = list_detail.find_all('li')
        for item in items:
            text = item.text.strip().split(' ')
            if len(text) >= 2:
                key = text[0] # '후기', '별점평균', '팔로워'
                value = text[1] # '162', '4.1', '5'
                review_stats[key] = value

    # 리뷰 작성일
    review_date_tag = temp_rev.select_one('.txt_date')
    review_date = review_date_tag.text.strip() if review_date_tag else "N/A"

    # 별점 (screen_out 클래스 중 두 번째에 텍스트 별점이 있음)
    rating_tag = temp_rev.select('.starred_grade .screen_out')
    # 두 번째 screen_out 태그에 실제 숫자가 들어있음 (별점 1.0)
    rating = rating_tag[1].text.strip() if len(rating_tag) > 1 else "N/A"

    # 리뷰 내용
    review_content_tag = temp_rev.select_one('.desc_review')
    if review_content_tag:
        # <p class="desc_review">텍스트 내용 <span class="btn_more">더보기</span></p>
        # p 태그의 첫 번째 자식 요소가 우리가 원하는 텍스트일 가능성이 높음.
        review_content_parts = [
            str(c) for c in review_content_tag.contents if c.name != 'span' and isinstance(c, str)
        ]
        review_content = ''.join(review_content_parts).replace('\n', '').strip()    
    else:
        review_content = "N/A"

    temp_rev_list.append(store_name)        # 가게 이름
    temp_rev_list.append(store_category)    # 가게 분류
    temp_rev_list.append(store_id)          # 카카오맵 ID
    temp_rev_list.append(reviewer_name)     # 리뷰어 이름
    temp_rev_list.append(reviewer_level)    # 리뷰어 레벨
    temp_rev_list.append(review_stats.get('후기', 'N/A'))       # 후기 개수
    temp_rev_list.append(review_stats.get('별점평균', 'N/A'))   # 별점 평균
    temp_rev_list.append(review_stats.get('팔로워', 'N/A'))     # 팔로워 수
    temp_rev_list.append(review_date)     # 리뷰 작성일
    temp_rev_list.append(rating)     # 별점
    temp_rev_list.append(review_content)    # 리뷰 내용

    # 리뷰 사진 URL
    photo_urls = []
    # .list_photo 클래스를 가진 ul 태그 안의 모든 img 태그를 찾습니다.
    # CSS Selector: .list_photo img
    img_tags = temp_rev.select('.list_photo img.img_g')

    if img_tags:
        for img_tag in img_tags:
            # img 태그의 'src' 속성 값을 가져옵니다.
            if 'src' in img_tag.attrs:
                photo_url = img_tag['src']
                photo_urls.append(photo_url)

        temp_rev_list.append(photo_urls)                
    else:
        temp_rev_list.append("N/A")
            
    return temp_rev_list

print("### 리뷰 수집을 시작합니다. ###")

### 코드 본문 시작점 ###
try:
    store_counter = 1
    for url in url_list:
        print(f"\n--- 새로운 가게 처리 시작: {url} ---")
        driver.get(url)
        time.sleep(2)

        ### '후기' 탭 유무 확인 및 클릭
        print("페이지 로드 중... '후기' 탭을 확인합니다.")
        review_tab_found_and_clicked = False
        potential_review_tabs = driver.find_elements(By.CSS_SELECTOR, 'a.link_tab[href="#comment"]')
        
        if potential_review_tabs:
            # 요소가 발견되었다면, 이제 클릭 가능한지 확인하고 클릭
            try:
                review_tab_button = WebDriverWait(driver, 5).until(
                    EC.element_to_be_clickable(potential_review_tabs[0]) # 첫 번째 요소를 대상으로
                )
                review_tab_button.click()
                print("'후기' 탭을 클릭했습니다.")
                review_tab_found_and_clicked = True
                time.sleep(1) # '후기' 탭 클릭 후 페이지 내용이 업데이트될 시간

            except Exception as e:
                print(f"$$$ '후기' 탭은 찾았으나 클릭할 수 없습니다.: {e} 건너뛰고 다음 가게로 넘어갑니다. $$$\n")
                continue # 다음 가게로 넘어가기

        else:
            print(f"$$$ '후기' 탭이 없습니다. 다음 가게로 넘어갑니다. $$$\n")
            continue # 다음 가게로 넘어가기

        ## 후기 20개 초과 시 스크롤링 
        # 페이지 로딩 대기 (필요시)
        WebDriverWait(driver, 3).until(EC.presence_of_all_elements_located((By.CLASS_NAME, "info_num")))
        # print(f"'{target_url}' 페이지 로드 완료.")

        ## 총 후기 갯수 체크. 20개 이상 시 스크롤 시작
        review_counter_elements = driver.find_elements(By.CLASS_NAME, "info_num")
        review_counter = int(review_counter_elements[0].text)    # 페이지 상단 후기 갯수. ([1]은 리뷰(블로그)갯수)

        if review_counter <= 20:
            print("### 후기 20개 미만. 스크롤 없이 다음 작업을 진행합니다. ###")

        else:
            # 스크롤 관련 변수 초기화
            last_height = driver.execute_script("return document.body.scrollHeight") # 초기 스크롤 높이
            scroll_count = 0 # 스크롤 횟수 추적
            max_scrolls = 100 # 무한 루프 방지용 최대 스크롤 횟수 (선택 사항)

            print("후기 갯수 20개 초과, 스크롤을 시작합니다...")

            try:
                while True:
                    scroll_count += 1
                    # print(f"--- 스크롤 시도 #{scroll_count} ---")

                    ## 페이지 맨 아래로 스크롤 및 새로운 내용 로드될 때 까지 대기
                    driver.execute_script("window.scrollTo(0, document.body.scrollHeight);")
                    time.sleep(2) # 2초대기

                    ## 새로운 스크롤 높이 가져오기 및 이전 스크롤 높이와 비교
                    new_height = driver.execute_script("return document.body.scrollHeight")

                    if new_height == last_height:
                        # print("더 이상 새로운 내용이 로드되지 않습니다. 스크롤 중단.")
                        break # 높이가 변하지 않으면 루프 종료
                    else:
                        # print(f"스크롤 높이 변경: {last_height} -> {new_height}. 계속 스크롤.")
                        last_height = new_height    # 다음 비교를 위해 높이 업데이트

                    # 최대 스크롤 횟수 제한 (선택 사항)
                    if scroll_count >= max_scrolls:
                        # print(f"최대 스크롤 횟수 ({max_scrolls})에 도달했습니다. 스크롤 중단.")
                        break

            except Exception as e:
                print(f"\n스크롤 중 오류 발생: {e}")

            finally:
                print("## 더 이상 새로운 후기가 로드되지 않습니다. 스크롤 완료 ##")
  
        ### '후기' 탭이 열렸으면 리뷰 내용에서 '더보기' 버튼 확장
        if review_tab_found_and_clicked:
            print("'더보기' 버튼을 확인하고 확장합니다.")
            clicked_more_buttons_count = 0
            
            # '더보기' 버튼 존재 여부를 빠르게 확인하고, 없으면 바로 다음 과정으로 이동
            potential_more_buttons = driver.find_elements(By.CSS_SELECTOR, 'ul.list_review span.btn_more')
            
            more_buttons_to_click = [
                btn for btn in potential_more_buttons if btn.text.strip() == '더보기'
            ]

            if not more_buttons_to_click:
                print("'더보기' 버튼이 없어 다음 작업을 진행합니다.")
                # '더보기' 버튼이 없으므로, 클릭 과정 없이 바로 다음 작업으로 진행합니다.
            else:
                print(f"총 {len(more_buttons_to_click)}개의 '더보기' 버튼을 확장")
                
                for i, button_element in enumerate(more_buttons_to_click):
                    try:
                        # 클릭 가능한 상태인지 확인 (JavaScript 클릭에 대한 추가적인 방어)
                        WebDriverWait(driver, 5).until(EC.element_to_be_clickable(button_element))
                        
                        driver.execute_script("arguments[0].scrollIntoView(true);", button_element)
                        driver.execute_script("arguments[0].click();", button_element)
                        
                        # print(f"  - [{i+1}/{len(more_buttons_to_click)}] '더보기' 버튼 클릭 성공.")
                        clicked_more_buttons_count += 1
                        time.sleep(0.1) # 클릭 후 DOM 업데이트를 위한 짧은 대기
                        
                    except Exception as click_error:
                        print(f"  - [{i+1}/{len(more_buttons_to_click)}] 버튼 클릭 실패: {click_error}")

                # print(f"총 {clicked_more_buttons_count}개의 '더보기' 버튼을 성공적으로 클릭했습니다.")
                
        # 4. 모든 '더보기' 버튼 확장 후 최종 HTML 파싱 및 데이터 추출
        # print(f"--- {url} 가게의 모든 '더보기' 버튼 클릭 작업 완료. 최종 데이터 추출을 준비합니다. ---")
        
        ### 파싱 및 리뷰 수집 시작
        html = driver.page_source
        soup = BeautifulSoup(html, 'html.parser')
        # time.sleep(0.2)        

        ## 가게 이름 가져오기
        title_info_tag = soup.select('#mainContent > div.top_basic > div.info_main > div.unit_info')
        store_name = title_info_tag[0].contents[0].contents[1]
        store_category = title_info_tag[0].contents[2].contents[1]
        store_id = url.split('/')[-1]

        ## 현재 크롤링 중인 가게 이름 표시 ##
        print("## no.", store_counter, " 사업장이름:",store_name ,"/ 분류:",store_category, "/ 카카오맵ID :",store_id , "##")

        ## 리뷰 그룹 가져오기
        review_group = soup.select('#mainContent > div.main_detail > div.detail_cont > div.section_comm.section_review > div.group_review > ul')

        rev_cnt = 0     # 리뷰 수 카운터
        start_perf_counter = time.perf_counter()    # 시간 측정용
        while review_group:
            if rev_cnt >= len(review_group[0].contents)-1:
                break

            temp_rev = review_group[0].contents[rev_cnt]
            time.sleep(0.1)
            temp_rev_list = all_review_scraping(temp_rev, rev_cnt)   

            print(temp_rev_list)    # 스크래핑한 리뷰 리스트 출력
            review_df.loc[len(review_df)] = temp_rev_list   # 사전 지정 DF에 추가
            rev_cnt += 1
            # time.sleep(0.5)

        end_perf_counter = time.perf_counter()
        elapsed_perf_time = end_perf_counter - start_perf_counter
        print(f"===== 걸린 시간 : {elapsed_perf_time:.2f} 초 =====") # 걸린 시간 표시

        store_counter += 1

except Exception as main_error:
    print(f"\n스크립트 실행 중 치명적인 오류 발생: {main_error}")

finally:
    driver.quit()
    print('** 리뷰 수집 완료. WebDriver를 종료합니다. **')


### 리뷰 수집을 시작합니다. ###

--- 새로운 가게 처리 시작: https://place.map.kakao.com/243028981 ---
페이지 로드 중... '후기' 탭을 확인합니다.
$$$ '후기' 탭이 없습니다. 다음 가게로 넘어갑니다. $$$


--- 새로운 가게 처리 시작: https://place.map.kakao.com/180472632 ---
페이지 로드 중... '후기' 탭을 확인합니다.
'후기' 탭을 클릭했습니다.
### 후기 20개 미만. 스크롤 없이 다음 작업을 진행합니다. ###
'더보기' 버튼을 확인하고 확장합니다.
'더보기' 버튼이 없어 다음 작업을 진행합니다.
## no. 1  사업장이름: 멜랑커피 연남 / 분류: 카페 / 카카오맵ID : 180472632 ##
['멜랑커피 연남', '카페', '180472632', 'entp', '32', '61', '4.1', '12', '2025.05.28.', '5.0', 'N/A', 'N/A']
===== 걸린 시간 : 0.11 초 =====

--- 새로운 가게 처리 시작: https://place.map.kakao.com/821235252 ---
페이지 로드 중... '후기' 탭을 확인합니다.
'후기' 탭을 클릭했습니다.
### 후기 20개 미만. 스크롤 없이 다음 작업을 진행합니다. ###
'더보기' 버튼을 확인하고 확장합니다.
총 6개의 '더보기' 버튼을 확장
## no. 2  사업장이름: 순대일번지 / 분류: 순대 / 카카오맵ID : 821235252 ##
['순대일번지', '순대', '821235252', '댕', '4', '2', '1.5', '1', '2025.05.07.', '2.0', '굳이...  평점이 왜 높은지 모르겠는...  밥도 설익고 식었고..국물이 그렇게 구미가 당기는지도 모르겠습니다ㅠㅠ 개인적인 의견입니다', 'N/A']
['순대일번지', '순대', '821235252', '리브흐', '21', '47', '5', '0', '2025.03.20.

In [11]:
review_df

사업장명  분류     카카오맵ID   리뷰어이름 리뷰어레벨 후기개수 별점평균 팔로워수          작성일   별점  \
0      멜랑커피 연남  카페  180472632    entp    32   61  4.1   12  2025.05.28.  5.0   
1        순대일번지  순대  821235252       댕     4    2  1.5    1  2025.05.07.  2.0   
2        순대일번지  순대  821235252     리브흐    21   47    5    0  2025.03.20.  5.0   
3        순대일번지  순대  821235252     마르스    32   80  3.9   25  2025.02.27.  4.0   
4        순대일번지  순대  821235252  여행 지킴이    32  116  4.7    1  2025.02.10.  5.0   
...        ...  ..        ...     ...   ...  ...  ...  ...          ...  ...   
19784    코리아식당  한식   15742085     예민보    27   68  3.6    1  2019.05.05.  2.0   
19785    코리아식당  한식   15742085      Ml    25  146  3.9    2  2019.02.10.  5.0   
19786    코리아식당  한식   15742085      ㅊㅇ    28   93  3.9    1  2018.08.07.  4.0   
19787    코리아식당  한식   15742085      으뜸    22   70    4    1  2017.11.02.  5.0   
19788    코리아식당  한식   15742085     최윤석    11  329    4    5  2016.03.18.  4.0   

                                                    리뷰내용  \
0                                                    N/A   
1      굳이...  평점이 왜 높은지 모르겠는...  밥도 설익고 식었고..국물이 그렇게 ...   
2             가게이름이 납득이갑니다안짜고요 양많아요양념으로 범벅하는 순대국 아니라 좋아요   
3      순대국특 먹었어요.다대기 들어있으니까 일단 먹어보고 싱거우면 새우젖으로 간해서 드세...   
4      여행타임tv를 운영하는 크리에이터입니다서울시내 순대국집 100군데를 다녀본바로 여긴...   
...                                                  ...   
19784                                       차돌박이 된장찌개 맹탕   
19785                                  가장 점심 먹고 싶은 집중 하나   
19786    뭘 시켜도 맛있고 밥집으로도 술집으로도 훌륭함.곱창찌개랑 돈까스 두부김치 전도 맛있음   
19787        점심 12시 넘으면 줄 서야해요. 이거저거 맛있는데 곱창찌개는 정말 맛있어요.   
19788                                                N/A   

                                                   사진URL  
0                                                    N/A  
1                                                    N/A  
2                                                    N/A  
3      [//img1.kakaocdn.net/cthumb/local/C280x280.q50...  
4      [//img1.kakaocdn.net/cthumb/local/C280x280.q50...  
...                                                  ...  
19784                                                N/A  
19785                                                N/A  
19786                                                N/A  
19787                                                N/A  
19788                                                N/A  

[19789 rows x 12 columns]

In [12]:
## csv 파일로 저장
review_df.to_csv("kakaomap_yeonnam_review_scrap(0530).csv", index=False, encoding="utf-8-sig")


In [13]:
## 정제용 DF 복제
filtered_df = review_df.copy()
filtered_df.head(10)

사업장명  분류     카카오맵ID    리뷰어이름 리뷰어레벨 후기개수 별점평균 팔로워수          작성일   별점  \
0  멜랑커피 연남  카페  180472632     entp    32   61  4.1   12  2025.05.28.  5.0   
1    순대일번지  순대  821235252        댕     4    2  1.5    1  2025.05.07.  2.0   
2    순대일번지  순대  821235252      리브흐    21   47    5    0  2025.03.20.  5.0   
3    순대일번지  순대  821235252      마르스    32   80  3.9   25  2025.02.27.  4.0   
4    순대일번지  순대  821235252   여행 지킴이    32  116  4.7    1  2025.02.10.  5.0   
5    순대일번지  순대  821235252       인혜     3    1    5    0  2025.02.08.  5.0   
6    순대일번지  순대  821235252       동환    21   30  4.6    2  2025.02.08.  5.0   
7    순대일번지  순대  821235252  박덕동 곽종필     8    6  3.8    0  2025.02.07.  3.0   
8    순대일번지  순대  821235252    맥아리장군    16   21  1.8    1  2025.01.04.  1.0   
9    순대일번지  순대  821235252      김희성     2    5    5    0  2024.11.29.  5.0   

                                                리뷰내용  \
0                                                N/A   
1  굳이...  평점이 왜 높은지 모르겠는...  밥도 설익고 식었고..국물이 그렇게 ...   
2         가게이름이 납득이갑니다안짜고요 양많아요양념으로 범벅하는 순대국 아니라 좋아요   
3  순대국특 먹었어요.다대기 들어있으니까 일단 먹어보고 싱거우면 새우젖으로 간해서 드세...   
4  여행타임tv를 운영하는 크리에이터입니다서울시내 순대국집 100군데를 다녀본바로 여긴...   
5  연남동에서 순대국 처음 먹어봤는데 생각 이상으로 국물이 깔끔하고 고기도 많았습니다!...   
6  주에 최소 한번은 순대국 수혈해야 살수있는사람인데집근처에 있길래 한번가봤는데 너무 ...   
7                                 김치가 너무 달고 순대도너무적었음   
8  제가 딱 한마디로 표현하겠습니다 여기는 순대국을 단 한번도 안 먹어본 사장님이 운영...   
9                                                N/A   

                                               사진URL  
0                                                N/A  
1                                                N/A  
2                                                N/A  
3  [//img1.kakaocdn.net/cthumb/local/C280x280.q50...  
4  [//img1.kakaocdn.net/cthumb/local/C280x280.q50...  
5  [//img1.kakaocdn.net/cthumb/local/C280x280.q50...  
6                                                N/A  
7                                                N/A  
8                                                N/A  
9                                                N/A

In [14]:
## 사진URL 행의 리스트 -> 문자열 전환

# 셀의 값이 리스트인지 확인하고, 리스트이면 join()으로 문자열 변환, 아니면 원래 값 유지
filtered_df['사진URL'] = filtered_df['사진URL'].apply(lambda x: ','.join(x) if isinstance(x, list) else x)
filtered_df.head(15)

사업장명  분류     카카오맵ID        리뷰어이름 리뷰어레벨 후기개수 별점평균 팔로워수          작성일  \
0   멜랑커피 연남  카페  180472632         entp    32   61  4.1   12  2025.05.28.   
1     순대일번지  순대  821235252            댕     4    2  1.5    1  2025.05.07.   
2     순대일번지  순대  821235252          리브흐    21   47    5    0  2025.03.20.   
3     순대일번지  순대  821235252          마르스    32   80  3.9   25  2025.02.27.   
4     순대일번지  순대  821235252       여행 지킴이    32  116  4.7    1  2025.02.10.   
5     순대일번지  순대  821235252           인혜     3    1    5    0  2025.02.08.   
6     순대일번지  순대  821235252           동환    21   30  4.6    2  2025.02.08.   
7     순대일번지  순대  821235252      박덕동 곽종필     8    6  3.8    0  2025.02.07.   
8     순대일번지  순대  821235252        맥아리장군    16   21  1.8    1  2025.01.04.   
9     순대일번지  순대  821235252          김희성     2    5    5    0  2024.11.29.   
10    순대일번지  순대  821235252  ilililiiiil    19   43  4.2    0  2024.11.16.   
11    순대일번지  순대  821235252           뮴뮴    11   22    5    1  2024.11.01.   
12    순대일번지  순대  821235252  Boink (김봉균)    53  276  4.1  239  2024.10.26.   
13    순대일번지  순대  821235252          TEO    29   68  4.1    1  2024.09.29.   
14    순대일번지  순대  821235252       MW BAK    30   50  3.8    8  2024.07.26.   

     별점                                               리뷰내용  \
0   5.0                                                N/A   
1   2.0  굳이...  평점이 왜 높은지 모르겠는...  밥도 설익고 식었고..국물이 그렇게 ...   
2   5.0         가게이름이 납득이갑니다안짜고요 양많아요양념으로 범벅하는 순대국 아니라 좋아요   
3   4.0  순대국특 먹었어요.다대기 들어있으니까 일단 먹어보고 싱거우면 새우젖으로 간해서 드세...   
4   5.0  여행타임tv를 운영하는 크리에이터입니다서울시내 순대국집 100군데를 다녀본바로 여긴...   
5   5.0  연남동에서 순대국 처음 먹어봤는데 생각 이상으로 국물이 깔끔하고 고기도 많았습니다!...   
6   5.0  주에 최소 한번은 순대국 수혈해야 살수있는사람인데집근처에 있길래 한번가봤는데 너무 ...   
7   3.0                                 김치가 너무 달고 순대도너무적었음   
8   1.0  제가 딱 한마디로 표현하겠습니다 여기는 순대국을 단 한번도 안 먹어본 사장님이 운영...   
9   5.0                                                N/A   
10  5.0                            순대 진짜 맛있네요 그리고 밥이 무한리필임   
11  5.0  진한 국물, 부드러운 고기, 쫄깃+부드러운 머릿고기, 통통한 순대, 아삭한 김치. ...   
12  4.0  The 순대국 was delicious. The 순대 wasn't the store...   
13  5.0  먹고나서도 속편하고 순대자체가 제대로인 식당을 찾은것 같네요~ 다음엔 수육 혹은 순...   
14  4.0  이곳에 아쉬움은 2층에 있다는 점이다.술한잔 마신이들이 2층을 올라갓다 내려가긴 여...   

                                                사진URL  
0                                                 N/A  
1                                                 N/A  
2                                                 N/A  
3   //img1.kakaocdn.net/cthumb/local/C280x280.q50/...  
4   //img1.kakaocdn.net/cthumb/local/C280x280.q50/...  
5   //img1.kakaocdn.net/cthumb/local/C280x280.q50/...  
6                                                 N/A  
7                                                 N/A  
8                                                 N/A  
9                                                 N/A  
10                                                N/A  
11                                                N/A  
12  //img1.kakaocdn.net/cthumb/local/C280x280.q50/...  
13  //img1.kakaocdn.net/cthumb/local/C280x280.q50/...  
14  //img1.kakaocdn.net/cthumb/local/C280x280.q50/...

In [15]:
## 중복 제거 전 길이 확인
len(filtered_df)

19789

In [16]:
## 중복데이터 제거
filtered_df = filtered_df.drop_duplicates()

In [17]:
## 중복데이터 제거 후 길이 확인
len(filtered_df)

19002

In [18]:
## '분류'행의 요소들 확인
pd.options.display.max_rows = 100
print(filtered_df['분류'].value_counts())

분류
양식           1793
카페           1660
일본식라면        1165
일식           1107
한식           1066
중국요리          932
일본식주점         926
태국음식          916
디저트카페         655
호프,요리주점       646
칵테일바          581
피자            577
이탈리안          548
멕시칸,브라질       434
육류,고기         384
회             350
초밥,롤          343
돈까스,우동        281
와인바           276
일식집           265
술집            264
제과,베이커리       258
퓨전요리          237
햄버거           237
동남아음식         226
중식            218
샐러드           213
커피전문점         184
국수            175
양꼬치           168
치킨            167
아이스크림         143
찌개,전골         136
인도음식          126
분식            122
베트남음식         111
닭요리           101
곱창,막창          99
국밥             80
서점             73
삼겹살            68
떡볶이            62
오뎅바            59
스페인음식          52
장어             50
해물,생선          47
참치회            47
실내포장마차         39
간식             35
한식뷔페           32
쌈밥             29
식품             18
즉석사진           17
초콜릿            17
퓨전일식           16
피부과    

In [19]:
filtered_df.info()

<class 'pandas.core.frame.DataFrame'>
Index: 19002 entries, 0 to 19788
Data columns (total 12 columns):
 #   Column  Non-Null Count  Dtype 
---  ------  --------------  ----- 
 0   사업장명    19002 non-null  object
 1   분류      19002 non-null  object
 2   카카오맵ID  19002 non-null  object
 3   리뷰어이름   19002 non-null  object
 4   리뷰어레벨   19002 non-null  object
 5   후기개수    19002 non-null  object
 6   별점평균    19002 non-null  object
 7   팔로워수    19002 non-null  object
 8   작성일     19002 non-null  object
 9   별점      19002 non-null  object
 10  리뷰내용    19002 non-null  object
 11  사진URL   19002 non-null  object
dtypes: object(12)
memory usage: 1.9+ MB


In [20]:
## 기본정제된 DF(filtered_df) csv 파일로 저장
filtered_df.to_csv("kakaomap_yeonnam_reviews_final(0530).csv", index=False, encoding="utf-8-sig")
